In [1]:
import os, sys, random, zipfile, io
from pathlib import Path

import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

import matplotlib.pyplot as plt
from matplotlib.ticker import AutoMinorLocator

from sklearn.model_selection import train_test_split

SEED = 42
tf.keras.utils.set_random_seed(SEED)
np.random.seed(SEED)
random.seed(SEED)


ZIP_URL = "https://prod-dcd-datasets-cache-zipfiles.s3.eu-west-1.amazonaws.com/xz4xhrc4yr-7.zip"


BASE_DIR = Path.cwd()
DATA_DIR = BASE_DIR / "pd_data"
ZIP_PATH = DATA_DIR / "pd.zip"
RAW_DIR = DATA_DIR / "pd_raw"


MODEL_CANDIDATES = [
    BASE_DIR / "fine_tuned.keras",
    Path("/mnt/data/fine_tuned.keras"),
]


IMG_SIZE = (224, 224)
BATCH = 32
AUTOTUNE = tf.data.AUTOTUNE

COLS, ROWS = 5, 2
N_SAMPLES = COLS * ROWS

def safe_mkdir(path: Path):
    path.mkdir(parents=True, exist_ok=True)

def download_file(url: str, dest: Path):
    import urllib.request
    if dest.exists() and dest.stat().st_size > 0:
        print(f"[download] Reusing {dest} (already exists).")
        return dest
    print(f"[download] Fetching {url} -> {dest} ...")
    with urllib.request.urlopen(url) as r, open(dest, "wb") as f:
        f.write(r.read())
    print("[download] Done.")
    return dest

def extract_zip(zip_path: Path, out_dir: Path):
    if out_dir.exists() and any(out_dir.iterdir()):
        print(f"[extract] Reusing extracted data in {out_dir}.")
        return out_dir
    print(f"[extract] Extracting {zip_path} -> {out_dir} ...")
    safe_mkdir(out_dir)
    with zipfile.ZipFile(zip_path, 'r') as zf:
        zf.extractall(out_dir)
    print("[extract] Done.")
    return out_dir

IMG_EXTS = {".png", ".jpg", ".jpeg", ".bmp", ".tif", ".tiff"}
LABEL_CANON = {
    "internal": "internal",
    "corona": "corona",
    "surface": "surface",
    "superficial": "surface",
}

def find_label_from_path(path: Path):
    for part in reversed(path.parts):
        key = part.lower()
        if key in LABEL_CANON:
            return LABEL_CANON[key]
    lower = [p.lower() for p in path.parts]
    for key in LABEL_CANON:
        if key in lower:
            return LABEL_CANON[key]
    return None

def load_image(path, label):
    img = tf.io.read_file(path)
    img = tf.image.decode_image(img, channels=3, expand_animations=False)
    img = tf.image.resize(img, IMG_SIZE, antialias=True)
    img.set_shape((*IMG_SIZE, 3))
    return img, label

def make_ds(paths, labels, training=False):
    ds = tf.data.Dataset.from_tensor_slices((paths, labels))
    if training:
        ds = ds.shuffle(len(paths), seed=SEED, reshuffle_each_iteration=True)
    ds = ds.map(load_image, num_parallel_calls=AUTOTUNE)
    ds = ds.batch(BATCH).prefetch(AUTOTUNE)
    return ds


safe_mkdir(DATA_DIR)
zip_path = download_file(ZIP_URL, ZIP_PATH)
extract_zip(zip_path, RAW_DIR)

all_imgs = []
for p in RAW_DIR.rglob("*"):
    if p.is_file() and p.suffix.lower() in IMG_EXTS:
        lbl = find_label_from_path(p.parent)
        if lbl is not None:
            all_imgs.append((str(p), lbl))

if not all_imgs:
    raise RuntimeError("No labeled images found. Please check the dataset structure after extraction.")

print(f"Found {len(all_imgs)} labeled images.")
labels_sorted = sorted(set(lbl for _, lbl in all_imgs))
print("Detected labels:", labels_sorted)

label_to_id = {lbl:i for i, lbl in enumerate(labels_sorted)}
id_to_label = {i:lbl for lbl, i in label_to_id.items()}

paths = np.array([p for p, _ in all_imgs])
y_text = np.array([lbl for _, lbl in all_imgs])
y = np.array([label_to_id[lbl] for lbl in y_text])

X_train, X_tmp, y_train, y_tmp = train_test_split(
    paths, y, test_size=0.30, random_state=SEED, stratify=y
)
X_test, X_val, y_test, y_val = train_test_split(
    X_tmp, y_tmp, test_size=0.5, random_state=SEED, stratify=y_tmp
)

print(f"Train: {len(X_train)}, Val: {len(X_val)}, Test: {len(X_test)}")

train_ds = make_ds(X_train, y_train, training=True)
val_ds   = make_ds(X_val,   y_val,   training=False)
test_ds  = make_ds(X_test,  y_test,  training=False)

model_path = None
for candidate in MODEL_CANDIDATES:
    if candidate.exists():
        model_path = candidate
        break

if model_path is None:
    raise FileNotFoundError(
        "Could not find 'fine_tuned.keras'. Place it in the same folder as this notebook "
        "or update MODEL_CANDIDATES to point to the file."
    )

print(f"Loading fine-tuned model from: {model_path}")
model = keras.models.load_model(model_path)


sample_idx = np.random.RandomState(SEED).choice(len(X_test), size=min(N_SAMPLES, len(X_test)), replace=False)
sample_paths = X_test[sample_idx]
sample_true  = y_test[sample_idx]

sample_ds = make_ds(sample_paths, sample_true, training=False)

probs = model.predict(sample_ds, verbose=0)
pred_ids = np.argmax(probs, axis=1)
true_ids = sample_true

plt.rcParams.update({
    "font.size": 20,
    "axes.titlesize": 20,
    "figure.dpi": 300,
})

fig = plt.figure(figsize=(COLS * 4.2, ROWS * 3.8))

for i, (img_path, true_id, pred_id) in enumerate(zip(sample_paths, true_ids, pred_ids)):
    ax = plt.subplot(ROWS, COLS, i + 1)

    img_bin = tf.io.read_file(img_path)
    img = tf.image.decode_image(img_bin, channels=3, expand_animations=False).numpy()
    ax.imshow(img)

    correct = (pred_id == true_id)
    title_color = "tab:green" if correct else "tab:red"

    true_lbl = id_to_label[int(true_id)]
    pred_lbl = id_to_label[int(pred_id)]
    ax.set_title(f"Label: {true_lbl}\nPrediction: {pred_lbl}", color=title_color, fontweight="bold")

    for spine in ax.spines.values():
        spine.set_edgecolor(title_color)
        spine.set_linewidth(2.0)
    ax.set_xticks([]); ax.set_yticks([])

plt.tight_layout(pad=1.0, w_pad=1.5, h_pad=2.5)

out_pdf = BASE_DIR / "fine_tuned_predictions_5x2.pdf"
plt.savefig(out_pdf, bbox_inches="tight")
print(f"Saved figure to: {out_pdf}")

plt.show()


[download] Reusing /content/pd_data/pd.zip (already exists).
[extract] Reusing extracted data in /content/pd_data/pd_raw.
Found 945 labeled images.
Detected labels: ['corona', 'internal', 'surface']
Train: 661, Val: 142, Test: 142
Loading fine-tuned model from: /content/fine_tuned.keras
Saved figure to: /content/fine_tuned_predictions_5x2.pdf
